This file runs estimates a Bertopic model for a single document to estimate topics based on a collection of texts. This demonstration used a single text divided into chunks to estimate a topic for each chunk obtained from the overall text. The result obtained is that the model divided the chunks based on the chapter topic.  

In [ ]:
# Import necessary packages
from bertopic import BERTopic
import os

In [92]:
# Set working directory to source file location
cwd = os.getcwd()

In [93]:
# Define file name and filetype
file = "Advanced Business Law and the Legal Environment"
filetype = "csv"

In [94]:
# Set path to data source
path = (f"{cwd}\\{file}.{filetype}")

In [95]:
path

'c:\\Users\\wesley.kammeraad\\Jupyter\\venvs\\.venv\\Advanced Business Law and the Legal Environment.csv'

In [96]:
# from datasets import load_dataset
# dataset = load_dataset("csv", data_files=path)["train"]

In [97]:
import pandas as pd
# Load data and convert to df
df = pd.read_csv(path, header=None, on_bad_lines='skip',
                 delimiter='\t')
df.head()

0
0  This text was adapted by The Saylor Foundation...
1  Our goal is to provide students with a textboo...
2  Traditional publishers often create confusion ...
3  This model eliminates the need for “families” ...
4  • Likewise, many sample legal forms are readil...

In [98]:
# Remove all empty chunks and convert columns to string
df = df.dropna()
df[0] = df.astype('string')

In [99]:
# Convert to list
data = df[0].to_list()

In [101]:
len(data)

6482

### Pre-calculate Embeddings

BERTopic works by converting documents into numerical values, called embeddings. This process can be very costly, especially if we want to iterate over parameters. Instead, we can calculate those embeddings once and feed them to BERTopic to skip calculating embeddings each time.

In [102]:
from sentence_transformers import SentenceTransformer

# Pre-calculate embeddings
embedding_model = SentenceTransformer("all-MiniLM-L6-v2")
embeddings = embedding_model.encode(data, show_progress_bar=True)

Batches: 100%|██████████| 203/203 [02:14<00:00,  1.51it/s]


In [103]:
embeddings

array([[-0.01638152,  0.00676624,  0.00054534, ..., -0.04211922,
        -0.00395832, -0.00820368],
       [ 0.0095285 ,  0.05150139,  0.01850576, ...,  0.05178741,
        -0.00513304,  0.02219538],
       [ 0.039744  , -0.02897582, -0.02476942, ..., -0.00812882,
         0.06490377,  0.02243245],
       ...,
       [-0.03986091, -0.0136036 , -0.02343549, ...,  0.01302176,
        -0.03136826, -0.00234434],
       [-0.02571853, -0.01341223,  0.0652972 , ...,  0.03353822,
        -0.09076405,  0.00094853],
       [-0.02004594, -0.06775193,  0.006017  , ..., -0.01436813,
        -0.04969005,  0.01133762]], dtype=float32)

### Preventing Stochastic Behavior


In BERTopic, we generally use a dimensionality reduction algorithm to reduce the size of the embeddings. This is done to prevent the curse of dimensionality to a certain degree.

As a default, this is done with UMAP which is an incredible algorithm for reducing dimensional space. However, by default, it shows stochastic behavior which creates different results each time you run it. To prevent that, we will need to set a random_state of the model before passing it to BERTopic.

As a result, we can now fully reproduce the results each time we run the model.

In [104]:
from umap.umap_ import UMAP
#from umap import UMAP

umap_model = UMAP(n_neighbors=15, n_components=5, min_dist=0.0, metric='cosine', random_state=42)

### Controlling Number of Topics

There is a parameter to control the number of topics, namely nr_topics. This parameter, however, merges topics after they have been created. It is a parameter that supports creating a fixed number of topics.

However, it is advised to control the number of topics through the cluster model which is by default HDBSCAN. HDBSCAN has a parameter, namely min_topic_size that indirectly controls the number of topics that will be created.

A higher min_topic_size will generate fewer topics and a lower min_topic_size will generate more topics.

In [105]:
from hdbscan import HDBSCAN

hdbscan_model = HDBSCAN(min_cluster_size=150, metric='euclidean', cluster_selection_method='eom', prediction_data=True)

### Improving Default Representation

The default representation of topics is calculated through c-TF-IDF. However, c-TF-IDF is powered by the CountVectorizer which converts text into tokens. Using the CountVectorizer, we can do a number of things:

* Remove stopwords
* Ignore infrequent words
* Increase

In other words, we can preprocess the topic representations after documents are assigned to topics. This will not influence the clustering process in any way.

Here, we will ignore English stopwords and infrequent words. Moreover, by increasing the n-gram range we will consider topic representations that are made up of one or two words.

In [106]:
from sklearn.feature_extraction.text import CountVectorizer
vectorizer_model = CountVectorizer(stop_words="english", min_df=1, ngram_range=(1, 3))

### Additional Representations

Previously, we have tuned the default representation but there are quite a number of other topic representations in BERTopic that we can choose from. From KeyBERTInspired and PartOfSpeech, to OpenAI's ChatGPT and open-source alternatives, many representations are possible.

In BERTopic, you can model many different topic representations simultanously to test them out and get different perspectives of topic descriptions. This is called multi-aspect topic modeling.

Here, we will demonstrate a number of interesting and useful representations in BERTopic:

* KeyBERTInspired
    * A method that derives inspiration from how KeyBERT works
* PartOfSpeech
    * Using SpaCy's POS tagging to extract words
* MaximalMarginalRelevance
    * Diversify the topic words
* OpenAI
    * Use ChatGPT to label our topics

In [107]:
import openai
from bertopic.representation import KeyBERTInspired, MaximalMarginalRelevance, OpenAI, PartOfSpeech

# KeyBERT
keybert_model = KeyBERTInspired()

# Part-of-Speech
pos_model = PartOfSpeech("en_core_web_sm")

# MMR
mmr_model = MaximalMarginalRelevance(diversity=0.3)

# GPT-3.5
prompt = """
I have a topic that contains the following documents:
[DOCUMENTS]
The topic is described by the following keywords: [KEYWORDS]

Based on the information above, extract a short but highly descriptive topic label of at most 5 words. Make sure it is in the following format:
topic: <topic label>
"""
client = openai.OpenAI(api_key="sk-...")
openai_model = OpenAI(client, model="gpt-3.5-turbo", exponential_backoff=True, chat=True, prompt=prompt)

# All representation models
representation_model = {
    "KeyBERT": keybert_model,
    # "OpenAI": openai_model,  # Uncomment if you will use OpenAI
    "MMR": mmr_model,
    "POS": pos_model
}

Training

In [108]:
from bertopic import BERTopic

topic_model = BERTopic(

  # Pipeline models
  embedding_model=embedding_model,
  umap_model=umap_model,
  hdbscan_model=hdbscan_model,
  vectorizer_model=vectorizer_model,
  representation_model=representation_model,

  # Hyperparameters
  top_n_words=10,
  verbose=True
)

topics, probs = topic_model.fit_transform(data, embeddings)

2024-12-20 10:48:48,789 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-12-20 10:49:02,825 - BERTopic - Dimensionality - Completed ✓
2024-12-20 10:49:02,828 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-12-20 10:49:03,338 - BERTopic - Cluster - Completed ✓
2024-12-20 10:49:03,343 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-12-20 10:49:11,825 - BERTopic - Representation - Completed ✓


In [109]:
topic_model.get_topic_info()

Topic  Count                                   Name  \
0     -1    905     -1_insurance_court_policy_property   
1      0   3774             0_law_court_goods_property   
2      1    862         1_bank_check_instrument_checks   
3      2    765  2_debtor_security_creditor_bankruptcy   
4      3    176       3_patent_use_copyright_trademark   

                                      Representation  \
0  [insurance, court, policy, property, martin, b...   
1  [law, court, goods, property, state, contract,...   
2  [bank, check, instrument, checks, holder, paym...   
3  [debtor, security, creditor, bankruptcy, chapt...   
4  [patent, use, copyright, trademark, trade, mar...   

                                             KeyBERT  \
0  [repossession, summary judgment, judgment, tru...   
1  [uniform commercial code, common law, laws, la...   
2  [bank, payment, deposit, banks, checks, transf...   
3  [bankruptcy, principal debtor, creditors, debt...   
4  [patent, patents, patented, intellectual prope...   

                                                 MMR  \
0  [property, bailee, lien, insured, mortgage, pl...   
1  [law, goods, property, contract, buyer, liabil...   
2  [bank, checks, signature, ucc, note, holder co...   
3  [debtor, creditor, bankruptcy, creditors, coll...   
4  [patent, copyright, trademark, invention, infr...   

                                                 POS  \
0  [insurance, court, policy, property, bailee, m...   
1  [law, court, goods, property, state, contract,...   
2  [bank, check, instrument, checks, holder, paym...   
3  [debtor, security, creditor, bankruptcy, chapt...   
4  [patent, use, copyright, trademark, trade, mar...   

                                 Representative_Docs  
0  [An insurer has grounds to avoid the contract ...  
1  [[1] Uniform Commercial Code, Section 9-109. [...  
2  [A person can become holder of an instrument w...  
3  [To what extent can the bankruptcy trustee tak...  
4  [A patent is a grant from government that give...

In [110]:
topic_model.get_topic(1, full=True)

{'Main': [('bank', np.float64(0.04165812351801411)),
  ('check', np.float64(0.037043828340300955)),
  ('instrument', np.float64(0.02888845228026114)),
  ('checks', np.float64(0.019167940114576794)),
  ('holder', np.float64(0.019045807159905996)),
  ('payment', np.float64(0.01722103186906013)),
  ('paper', np.float64(0.013927140267458667)),
  ('person', np.float64(0.013053857939905626)),
  ('indorsement', np.float64(0.01258596038502074)),
  ('pay', np.float64(0.011643020583658048))],
 'KeyBERT': [('bank', np.float32(0.48394266)),
  ('payment', np.float32(0.4812731)),
  ('deposit', np.float32(0.47616008)),
  ('banks', np.float32(0.4669138)),
  ('checks', np.float32(0.46554497)),
  ('transfers', np.float32(0.4291198)),
  ('stop payment', np.float32(0.39188027)),
  ('signature', np.float32(0.38792127)),
  ('transfer', np.float32(0.37629685)),
  ('cash', np.float32(0.3756617))],
 'MMR': [('bank', np.float64(0.04165812351801411)),
  ('checks', np.float64(0.019167940114576794)),
  ('signature

(Custom) Labels

In [112]:
# # Label the topics yourself
# topic_model.set_topic_labels({1: "Space Travel", 7: "Religion"})

# # or use one of the other topic representations, like KeyBERTInspired
# keybert_topic_labels = {topic: " | ".join(list(zip(*values))[0][:3]) for topic, values in topic_model.topic_aspects_["KeyBERT"].items()}
# topic_model.set_topic_labels(keybert_topic_labels)

# or ChatGPT's labels
#chatgpt_topic_labels = {topic: " | ".join(list(zip(*values))[0]) for topic, values in topic_model.topic_aspects_["OpenAI"].items()}
#chatgpt_topic_labels[-1] = "Outlier Topic"
#topic_model.set_topic_labels(chatgpt_topic_labels)

In [113]:
topic_model.get_topic_info()

Topic  Count                                   Name  \
0     -1    905     -1_insurance_court_policy_property   
1      0   3774             0_law_court_goods_property   
2      1    862         1_bank_check_instrument_checks   
3      2    765  2_debtor_security_creditor_bankruptcy   
4      3    176       3_patent_use_copyright_trademark   

                                      Representation  \
0  [insurance, court, policy, property, martin, b...   
1  [law, court, goods, property, state, contract,...   
2  [bank, check, instrument, checks, holder, paym...   
3  [debtor, security, creditor, bankruptcy, chapt...   
4  [patent, use, copyright, trademark, trade, mar...   

                                             KeyBERT  \
0  [repossession, summary judgment, judgment, tru...   
1  [uniform commercial code, common law, laws, la...   
2  [bank, payment, deposit, banks, checks, transf...   
3  [bankruptcy, principal debtor, creditors, debt...   
4  [patent, patents, patented, intellectual prope...   

                                                 MMR  \
0  [property, bailee, lien, insured, mortgage, pl...   
1  [law, goods, property, contract, buyer, liabil...   
2  [bank, checks, signature, ucc, note, holder co...   
3  [debtor, creditor, bankruptcy, creditors, coll...   
4  [patent, copyright, trademark, invention, infr...   

                                                 POS  \
0  [insurance, court, policy, property, bailee, m...   
1  [law, court, goods, property, state, contract,...   
2  [bank, check, instrument, checks, holder, paym...   
3  [debtor, security, creditor, bankruptcy, chapt...   
4  [patent, use, copyright, trademark, trade, mar...   

                                 Representative_Docs  
0  [An insurer has grounds to avoid the contract ...  
1  [[1] Uniform Commercial Code, Section 9-109. [...  
2  [A person can become holder of an instrument w...  
3  [To what extent can the bankruptcy trustee tak...  
4  [A patent is a grant from government that give...

Topic-Document Distribution

In [114]:
# `topic_distr` contains the distribution of topics in each document
topic_distr, _ = topic_model.approximate_distribution(data, window=8, stride=4)

100%|██████████| 7/7 [00:01<00:00,  4.68it/s]


In [115]:
# # Visualize the topic-document distribution for a single document
# topic_model.visualize_distribution(topic_distr[0])

In [116]:
# # Visualize the topic-document distribution for a single document
# topic_model.visualize_distribution(topic_distr[abstract_id], custom_labels=True)

In [117]:
# # Calculate the topic distributions on a token-level
# topic_distr, topic_token_distr = topic_model.approximate_distribution(abstracts[abstract_id], calculate_tokens=True)

# # Visualize the token-level distributions
# df = topic_model.visualize_approximate_distribution(abstracts[abstract_id], topic_token_distr[0])
# df

Outlier Reduction

In [118]:
# Reduce outliers
new_topics = topic_model.reduce_outliers(data, topics)

# Reduce outliers with pre-calculate embeddings instead
new_topics = topic_model.reduce_outliers(data, topics, strategy="embeddings", embeddings=embeddings)

100%|██████████| 1/1 [00:00<00:00,  2.65it/s]


Visualize Topics

In [119]:
topic_model.visualize_topics(custom_labels=True)

In [120]:
topic_model.visualize_hierarchy(custom_labels=True)

Visualize Documents

In [121]:
# Reduce dimensionality of embeddings, this step is optional but much faster to perform iteratively:
reduced_embeddings = UMAP(n_neighbors=10, n_components=4, min_dist=0.0, metric='cosine').fit_transform(embeddings)

In [122]:
reduced_embeddings[0]
len(reduced_embeddings)

6482

In [123]:
# Visualize the documents in 2-dimensional space and show the titles on hover instead of the abstracts
# NOTE: You can hide the hover with `hide_document_hover=True` which is especially helpful if you have a large dataset
topic_model.visualize_documents(data, reduced_embeddings=reduced_embeddings, custom_labels=True)

In [124]:
# We can also hide the annotation to have a more clear overview of the topics
topic_model.visualize_documents(data, reduced_embeddings=reduced_embeddings, custom_labels=True, hide_annotations=True)

Model Inference

In [125]:
topic_model.get_topic_info()

Topic  Count                                   Name  \
0     -1    905     -1_insurance_court_policy_property   
1      0   3774             0_law_court_goods_property   
2      1    862         1_bank_check_instrument_checks   
3      2    765  2_debtor_security_creditor_bankruptcy   
4      3    176       3_patent_use_copyright_trademark   

                                      Representation  \
0  [insurance, court, policy, property, martin, b...   
1  [law, court, goods, property, state, contract,...   
2  [bank, check, instrument, checks, holder, paym...   
3  [debtor, security, creditor, bankruptcy, chapt...   
4  [patent, use, copyright, trademark, trade, mar...   

                                             KeyBERT  \
0  [repossession, summary judgment, judgment, tru...   
1  [uniform commercial code, common law, laws, la...   
2  [bank, payment, deposit, banks, checks, transf...   
3  [bankruptcy, principal debtor, creditors, debt...   
4  [patent, patents, patented, intellectual prope...   

                                                 MMR  \
0  [property, bailee, lien, insured, mortgage, pl...   
1  [law, goods, property, contract, buyer, liabil...   
2  [bank, checks, signature, ucc, note, holder co...   
3  [debtor, creditor, bankruptcy, creditors, coll...   
4  [patent, copyright, trademark, invention, infr...   

                                                 POS  \
0  [insurance, court, policy, property, bailee, m...   
1  [law, court, goods, property, state, contract,...   
2  [bank, check, instrument, checks, holder, paym...   
3  [debtor, security, creditor, bankruptcy, chapt...   
4  [patent, use, copyright, trademark, trade, mar...   

                                 Representative_Docs  
0  [An insurer has grounds to avoid the contract ...  
1  [[1] Uniform Commercial Code, Section 9-109. [...  
2  [A person can become holder of an instrument w...  
3  [To what extent can the bankruptcy trustee tak...  
4  [A patent is a grant from government that give...

In [126]:
topic_model.get_topic_info()[['Topic', 'Name']]

Topic                                   Name
0     -1     -1_insurance_court_policy_property
1      0             0_law_court_goods_property
2      1         1_bank_check_instrument_checks
3      2  2_debtor_security_creditor_bankruptcy
4      3       3_patent_use_copyright_trademark

In [127]:
topic_model.get_params()

{'calculate_probabilities': False,
 'ctfidf_model': ClassTfidfTransformer(),
 'embedding_model': <bertopic.backend._sentencetransformers.SentenceTransformerBackend at 0x1930bc80aa0>,
 'hdbscan_model': HDBSCAN(min_cluster_size=150, prediction_data=True),
 'language': None,
 'low_memory': False,
 'min_topic_size': 10,
 'n_gram_range': (1, 1),
 'nr_topics': None,
 'representation_model': {'KeyBERT': KeyBERTInspired(),
  'MMR': MaximalMarginalRelevance(diversity=0.3),
  'POS': PartOfSpeech(model=<spacy.lang.en.English object at 0x000001930887A900>,
               pos_patterns=[[{'POS': 'ADJ'}, {'POS': 'NOUN'}], [{'POS': 'NOUN'}],
                             [{'POS': 'ADJ'}]])},
 'seed_topic_list': None,
 'top_n_words': 10,
 'umap_model': UMAP(angular_rp_forest=True, metric='cosine', min_dist=0.0, n_components=5, n_jobs=1, random_state=42, tqdm_kwds={'bar_format': '{desc}: {percentage:3.0f}%| {bar} {n_fmt}/{total_fmt} [{elapsed}]', 'desc': 'Epochs completed', 'disable': True}),
 'vectorize

In [137]:
topic_model._get_param_names()

['calculate_probabilities',
 'ctfidf_model',
 'embedding_model',
 'hdbscan_model',
 'language',
 'low_memory',
 'min_topic_size',
 'n_gram_range',
 'nr_topics',
 'representation_model',
 'seed_topic_list',
 'top_n_words',
 'umap_model',
 'vectorizer_model',
 'verbose',
 'zeroshot_min_similarity',
 'zeroshot_topic_list']

Save Topics: Topic Label + Numerical Label

In [138]:
chunk_topic = {
    "Data":data,
    "Topic": topics
    }

In [139]:
df_chunk_topic = pd.DataFrame(chunk_topic)
# df_chunk_topic['Topic'] = df_chunk_topic['Topic']+1

In [140]:
df_chunk_topic.loc[df_chunk_topic['Topic'] > -1]

Data  Topic
0     This text was adapted by The Saylor Foundation...      3
1     Our goal is to provide students with a textboo...      0
2     Traditional publishers often create confusion ...      3
3     This model eliminates the need for “families” ...      3
4     • Likewise, many sample legal forms are readil...      0
...                                                 ...    ...
6467                             c. breach of warranty       0
6475                         a. ordinary wear and tear       0
6476                            b. damage due to theft       0
6477                             c. intentional losses       0
6478                      d. damage due to earthquakes       0

[5577 rows x 2 columns]

In [141]:
topic_model.get_topic_info()[['Topic', 'Name']]

Topic                                   Name
0     -1     -1_insurance_court_policy_property
1      0             0_law_court_goods_property
2      1         1_bank_check_instrument_checks
3      2  2_debtor_security_creditor_bankruptcy
4      3       3_patent_use_copyright_trademark

In [142]:
topic_labels = topic_model.get_topic_info()[['Topic', 'Name']]

In [143]:
df_chunk_topic = df_chunk_topic.merge(topic_labels, on='Topic', how='left')

In [144]:
# df_chunk_topic = df_chunk_topic['Name'].rename('Label')

In [147]:
df_chunk_topic = df_chunk_topic.rename(columns={'Name': 'Label'})

In [152]:
df_chunk_topic = df_chunk_topic.drop('Topic', axis=1)

In [154]:
df_chunk_topic

Data  \
0     This text was adapted by The Saylor Foundation...   
1     Our goal is to provide students with a textboo...   
2     Traditional publishers often create confusion ...   
3     This model eliminates the need for “families” ...   
4     • Likewise, many sample legal forms are readil...   
...                                                 ...   
6477                             c. intentional losses    
6478                      d. damage due to earthquakes    
6479                                              1. c    
6480                                              2. d    
6481                                              3. d    

                                   Label  
0       3_patent_use_copyright_trademark  
1             0_law_court_goods_property  
2       3_patent_use_copyright_trademark  
3       3_patent_use_copyright_trademark  
4             0_law_court_goods_property  
...                                  ...  
6477          0_law_court_goods_property  
6478          0_law_court_goods_property  
6479  -1_insurance_court_policy_property  
6480  -1_insurance_court_policy_property  
6481  -1_insurance_court_policy_property  

[6482 rows x 2 columns]

In [153]:
df_chunk_topic.to_csv('Business-Law-Legal-Chunks-Topics.csv')